# Exploratory analysis

TODO:
- Understanding the reason for fake profiles can bring insight on how to catch them (could be trivial with prior knowledge, e.g., SEO hacking => URLs)
- Make casistics (e.g. author publishing with empty orcid, author publishing but not on OpenAIRE, etc.)
- Temporal dimension of any use?
- Can we access private info thanks to the OpenAIRE-ORCID agreement?


In [1]:
import pandas as pd
import ast
import tldextract
import numpy

import plotly
from plotly.offline import iplot, init_notebook_mode
import plotly.graph_objs as go
import plotly.express as px

init_notebook_mode(connected=True)
TOP_N = 0
TOP_RANGE = [0, 0]
def set_top_n(n):
    global TOP_N, TOP_RANGE
    TOP_N = n
    TOP_RANGE = [-.5, n - 1 + .5]

Notable solid ORCID iDs for explorative purposes:

In [2]:
AM = '0000-0002-5193-7851'
PP = '0000-0002-8588-4196'


Notable anomalies:

In [3]:
JOURNAL = '0000-0003-1815-5732'
NOINFO = '0000-0001-5009-2052'
VALID_NO_OA = '0000-0002-5154-6404' # True profile, but not in OpenAIRE
# todo: find group-shared ORCiD, if possible

Notable fake ORCID iDs:

In [4]:
SCAFFOLD = '0000-0001-5004-7761'
WHATSAPP = '0000-0001-6997-9470'
PENIS = '0000-0002-3399-7287'
BITCOIN = '0000-0002-7518-6845'
FITNESS_CHINA = '0000-0002-1234-835X' # URL record + employment
CANNABIS = '0000-0002-9025-8632'      # URL > 70 + works (REMOVED)
PLUMBER = '0000-0002-1700-8311'       # URL > 10 + works 

Load the dataset

In [5]:
df = pd.read_pickle('../data/processed/dataset.pkl')
df.head(5)

orcid  claimed  verified_email  verified_primary_email  \
0  0000-0001-5009-2052        1               1                       1   
1  0000-0001-5943-0732        1               1                       1   
2  0000-0001-6083-622x        1               1                       1   
3  0000-0001-6262-5709        1               1                       1   
4  0000-0001-6616-4890        1               1                       1   

  given_names family_name biography other_names urls primary_email  ...  \
0         NaN         NaN       NaN         NaN  NaN           NaN  ...   
1         NaN         NaN       NaN         NaN  NaN           NaN  ...   
2         NaN         NaN       NaN         NaN  NaN           NaN  ...   
3         NaN         NaN       NaN         NaN  NaN           NaN  ...   
4         NaN         NaN       NaN         NaN  NaN           NaN  ...   

  employment n_works works_source           activation_date  \
0        NaN       0          NaN  2019-06-05t20:25:43.066z   
1        NaN       0          NaN  2015-08-18t13:10:42.871z   
2        NaN       0          NaN  2019-01-21t10:55:27.997z   
3        NaN       0          NaN  2015-08-18t14:29:39.440z   
4        NaN       0          NaN  2015-08-13t01:59:51.802z   

           last_update_date  n_doi n_arxiv n_pmc n_other_pids  label  
0  2019-12-11t03:57:41.741z      0       0     0            0      0  
1  2016-06-15t01:05:19.986z      0       0     0            0      0  
2  2019-01-28t16:24:02.199z      0       0     0            0      0  
3  2017-06-21t07:18:20.787z      0       0     0            0      0  
4  2016-06-15t01:05:21.373z      0       0     0            0      0  

[5 rows x 24 columns]

Notable profiles inspection

In [6]:
df[df['orcid'] == AM]

orcid  claimed  verified_email  verified_primary_email  \
1575869  0000-0002-5193-7851        1               1                       1   

        given_names family_name  \
1575869      andrea    mannocci   

                                                 biography other_names  \
1575869  data scientist & researcher; scholarly knowled...         NaN   

                                                      urls  \
1575869  [[personal website, https://andremann.github.i...   

                       primary_email  ...  \
1575869  andrea.mannocci@isti.cnr.it  ...   

                                                employment n_works  \
1575869  [[research associate, istituto di scienza e te...      37   

                                              works_source  \
1575869  [scopus - elsevier, crossref metadata search, ...   

                  activation_date          last_update_date  n_doi n_arxiv  \
1575869  2017-09-12t14:28:33.467z  2021-03-09t08:32:47.840z     34       0   

        n_pmc n_other_pids  label  
1575869     0           60      1  

[1 rows x 24 columns]

In [7]:
df[df['orcid'] == WHATSAPP]

orcid  claimed  verified_email  verified_primary_email  \
6819986  0000-0001-6997-9470        1               1                       1   

        given_names family_name biography other_names  \
6819986       other    whatsapp       NaN         NaN   

                                                      urls primary_email  ...  \
6819986  [[otherwhatsapp, https://otherwhatsapp.com/], ...           NaN  ...   

        employment n_works works_source           activation_date  \
6819986        NaN       0          NaN  2020-10-07t10:37:12.237z   

                 last_update_date  n_doi n_arxiv n_pmc n_other_pids  label  
6819986  2020-10-08t02:32:03.935z      0       0     0            0      0  

[1 rows x 24 columns]

In [8]:
df.count()

orcid                     10916574
claimed                   10916574
verified_email            10916574
verified_primary_email    10916574
given_names               10886150
family_name               10601571
biography                   348649
other_names                 551482
urls                        707687
primary_email               123851
other_emails                 48306
keywords                    646400
external_ids               1301959
education                  2430233
employment                 2665092
n_works                   10916574
works_source               2721431
activation_date           10916574
last_update_date          10916574
n_doi                     10916574
n_arxiv                   10916574
n_pmc                     10916574
n_other_pids              10916574
label                     10916574
dtype: int64

In [9]:
df['orcid'].describe()

count                10916574
unique               10916574
top       0000-0001-8786-4765
freq                        1
Name: orcid, dtype: object

## Primary email

In [10]:
df['primary_email'].describe()

count                       123851
unique                      123848
top       patrick.davey@monash.edu
freq                             2
Name: primary_email, dtype: object

Dupe emails

In [11]:
df['primary_email'].dropna().loc[df['primary_email'].duplicated()]

6347224            maykin@owasp.org
7027865    patrick.davey@monash.edu
9529005      opercin@erbakan.edu.tr
Name: primary_email, dtype: object

In [12]:
df[df['primary_email'] == 'maykin@owasp.org']

orcid  claimed  verified_email  verified_primary_email  \
4450046  0000-0001-9855-1676        1               1                       1   
6347224  0000-0002-0836-2271        1               1                       1   

        given_names family_name biography other_names urls     primary_email  \
4450046      maykin    warasart       NaN         NaN  NaN  maykin@owasp.org   
6347224      maykin    warasart       NaN         NaN  NaN  maykin@owasp.org   

         ... employment n_works works_source           activation_date  \
4450046  ...        NaN       0          NaN  2020-10-23t17:51:51.925z   
6347224  ...        NaN       0          NaN  2020-09-15t04:43:55.709z   

                 last_update_date  n_doi n_arxiv n_pmc n_other_pids  label  
4450046  2021-01-01t15:00:52.053z      0       0     0            0      0  
6347224  2020-09-15t05:17:28.509z      0       0     0            0      0  

[2 rows x 24 columns]

In [13]:
df[df['primary_email'] == 'opercin@erbakan.edu.tr']

orcid  claimed  verified_email  verified_primary_email  \
6840791  0000-0002-2232-9638        1               1                       1   
9529005  0000-0003-0033-0918        1               1                       1   

        given_names family_name biography other_names urls  \
6840791       osman      perçin       NaN         NaN  NaN   
9529005       osman      perçin       NaN         NaN  NaN   

                  primary_email  ...  \
6840791  opercin@erbakan.edu.tr  ...   
9529005  opercin@erbakan.edu.tr  ...   

                                                employment n_works  \
6840791                                                NaN       0   
9529005  [[, necmettin erbakan university, konya, , tr,...       0   

        works_source           activation_date          last_update_date  \
6840791          NaN  2015-01-12t13:47:55.549z  2020-01-27t07:38:24.269z   
9529005          NaN  2015-10-13t05:47:12.014z  2020-12-25t13:52:03.976z   

         n_doi n_arxiv n_pmc n_other_pids  label  
6840791      0       0     0            0      0  
9529005      0       0     0            0      0  

[2 rows x 24 columns]

In [14]:
df[df['primary_email'] == 'patrick.davey@monash.edu']

orcid  claimed  verified_email  verified_primary_email  \
944993   0000-0002-9158-1757        1               1                       1   
7027865  0000-0002-8774-0030        1               1                       1   

        given_names family_name biography other_names urls  \
944993      patrick       davey       NaN         NaN  NaN   
7027865     patrick       davey       NaN         NaN  NaN   

                    primary_email  ...  \
944993   patrick.davey@monash.edu  ...   
7027865  patrick.davey@monash.edu  ...   

                                                employment n_works  \
944993   [[phd student, monash university, melbourne, ,...       0   
7027865  [[phd student, monash university, melbourne, v...       1   

        works_source           activation_date          last_update_date  \
944993           NaN  2019-05-09t23:01:02.170z  2019-08-20t03:00:17.844z   
7027865   [crossref]  2018-09-11t10:47:10.997z  2021-02-09t06:21:44.138z   

         n_doi n_arxiv n_pmc n_other_pids  label  
944993       0       0     0            0      0  
7027865      1       0     0            0      1  

[2 rows x 24 columns]

In [15]:
df['primary_email_domain'] = df[df.primary_email.notna()]['primary_email'].apply(lambda x: x.split('@')[1])

In [16]:
df['primary_email_domain'].describe()

count        123851
unique        17089
top       gmail.com
freq          26540
Name: primary_email_domain, dtype: object

In [17]:
top_primary_emails = df[['primary_email_domain', 'orcid']]\
                .groupby('primary_email_domain')\
                .count()\
                .sort_values('orcid', ascending=False)
top_primary_emails

orcid
primary_email_domain       
gmail.com             26540
hotmail.com            3769
yahoo.com              2614
163.com                2109
yuhs.ac                1132
...                     ...
imean-biotech.com         1
imec.msu.ru               1
imedea.uib-csic.es        1
imes.uni-hannover.de      1
zzuli.edu.cn              1

[17089 rows x 1 columns]

In [18]:
set_top_n(30)
data = [
    go.Bar(
        x=top_primary_emails[:TOP_N].index,
        y=top_primary_emails[:TOP_N]['orcid']
    )
]

layout = go.Layout(
    title='Top-%s email domains' % TOP_N,
    xaxis=dict(tickangle=45, tickfont=dict(size=12), range=TOP_RANGE)
)
fig = go.Figure(data=data, layout=layout)
plotly.offline.iplot(fig)

## Other emails

In [19]:
def extract_email_domains(lst):
    res = []
    for email in lst:
        res.append(email.split('@')[1])
    return res

In [20]:
df['other_email_domains'] = df[df.other_emails.notna()]['other_emails'].apply(lambda x: extract_email_domains(x))

In [21]:
df[df['other_email_domains'].notna()].head()

orcid  claimed  verified_email  verified_primary_email  \
34    0000-0002-5774-8947        1               1                       1   
1199  0000-0003-2877-5492        1               1                       0   
1995  0000-0001-8004-5054        1               1                       1   
2323  0000-0003-3048-4504        1               1                       1   
4461  0000-0001-9961-9732        1               1                       1   

     given_names  family_name biography                  other_names urls  \
34           NaN          NaN       NaN  [omah m. williams - duncan]  NaN   
1199   aliasghar  khosroabadi       NaN                          NaN  NaN   
1995     angiola      orlando       NaN                          NaN  NaN   
2323     apichat       saejio       NaN                          NaN  NaN   
4461    chunfeng          yun       NaN                          NaN  NaN   

                    primary_email  ...  \
34                            NaN  ...   
1199          khosroedc@yahoo.com  ...   
1995  angiola.orlando@mib.infn.it  ...   
2323                          NaN  ...   
4461             sallyycf@163.com  ...   

                                           works_source  \
34                                                  NaN   
1199                                [scopus - elsevier]   
1995                        [angiola orlando, crossref]   
2323                                [scopus - elsevier]   
4461  [multidisciplinary digital publishing institut...   

               activation_date          last_update_date n_doi n_arxiv  n_pmc  \
34    2014-03-07t04:34:39.598z  2019-05-21t17:08:12.202z     0       0      0   
1199  2018-01-19t13:40:29.874z  2019-12-11t02:19:08.160z     0       0      0   
1995  2015-08-31t09:12:02.349z  2020-06-22t14:22:31.786z    59       2      0   
2323  2016-03-06t08:54:15.121z  2020-08-28t08:31:15.790z     2       0      0   
4461  2016-11-22t07:55:23.863z  2019-11-26t02:29:35.104z     5       0      9   

     n_other_pids label primary_email_domain        other_email_domains  
34              0     0                  NaN                [gmail.com]  
1199            1     1            yahoo.com  [medsab.ac.ir, gmail.com]  
1995           53     1          mib.infn.it               [ge.infn.it]  
2323            4     0                  NaN         [eat.kmutnb.ac.th]  
4461            0     1              163.com               [pku.edu.cn]  

[5 rows x 26 columns]

In [22]:
df['n_emails'] = df['other_emails'].str.len()

In [23]:
emails_by_orcid = df.sort_values('n_emails', ascending=False)

In [24]:
set_top_n(30)
data = [
    go.Bar(
        x=emails_by_orcid[:TOP_N]['orcid'],
        y=emails_by_orcid[:TOP_N]['n_emails']
    )
]

layout = go.Layout(
    title='Top %s ORCID iDs by email' % TOP_N, 
    xaxis=dict(tickangle=45, tickfont=dict(size=12), range=TOP_RANGE)
)
fig = go.Figure(data=data, layout=layout)
plotly.offline.iplot(fig)

In [25]:
top_other_emails = df[['orcid', 'other_email_domains']]\
                        .explode('other_email_domains')\
                        .reset_index(drop=True)\
                        .groupby('other_email_domains')\
                        .count()\
                        .sort_values('orcid', ascending=False)

In [26]:
set_top_n(30)
data = [
    go.Bar(
        x=top_other_emails[:TOP_N].index,
        y=top_other_emails[:TOP_N]['orcid']
    )
]

layout = go.Layout(
    title='Top %s other email domains' % TOP_N, 
    xaxis=dict(tickangle=45, tickfont=dict(size=12), range=TOP_RANGE)
)
fig = go.Figure(data=data, layout=layout)
plotly.offline.iplot(fig)

## Email speculation

In [27]:
df[df['primary_email'].isna() & df['other_emails'].notna()]

orcid  claimed  verified_email  \
34        0000-0002-5774-8947        1               1   
2323      0000-0003-3048-4504        1               1   
7622      0000-0002-5612-7444        1               1   
7956      0000-0002-8943-0538        1               1   
10508     0000-0002-4022-0580        1               1   
...                       ...      ...             ...   
10915002  0000-0002-3715-3866        1               1   
10915305  0000-0003-1925-0141        1               1   
10915495  0000-0001-5526-3017        1               1   
10915820  0000-0002-9902-7953        1               1   
10916306  0000-0002-5126-5127        1               1   

          verified_primary_email    given_names       family_name biography  \
34                             1            NaN               NaN       NaN   
2323                           1        apichat            saejio       NaN   
7622                           1  friederike m.             hesse       NaN   
7956                           1            geo             sunny       NaN   
10508                          1    jean carlos    da silva gomes       NaN   
...                          ...            ...               ...       ...   
10915002                       1         joanna  korybut-orlowska       NaN   
10915305                       1          marco          ferretti       NaN   
10915495                       1          nadia           yacoubi       NaN   
10915820                       1   s m mahmudul             hasan       NaN   
10916306                       1        andonis         neophytou       NaN   

                          other_names  \
34        [omah m. williams - duncan]   
2323                              NaN   
7622                              NaN   
7956                              NaN   
10508                             NaN   
...                               ...   
10915002         [joanna gołębiewska]   
10915305                          NaN   
10915495                          NaN   
10915820                          NaN   
10916306                          NaN   

                                                       urls primary_email  \
34                                                      NaN           NaN   
2323                                                    NaN           NaN   
7622      [[midwifery care - milla hebammenpraxis, http:...           NaN   
7956                                                    NaN           NaN   
10508     [[currículo lattes, http://lattes.cnpq.br/0026...           NaN   
...                                                     ...           ...   
10915002                                                NaN           NaN   
10915305                                                NaN           NaN   
10915495                                                NaN           NaN   
10915820                                                NaN           NaN   
10916306                                                NaN           NaN   

          ...           activation_date          last_update_date n_doi  \
34        ...  2014-03-07t04:34:39.598z  2019-05-21t17:08:12.202z     0   
2323      ...  2016-03-06t08:54:15.121z  2020-08-28t08:31:15.790z     2   
7622      ...  2017-06-10t07:45:11.387z  2017-06-10t07:55:03.455z     0   
7956      ...  2019-11-30t14:08:11.221z  2020-05-15t09:06:25.637z     1   
10508     ...  2017-05-26t19:09:33.432z  2020-06-02t00:23:14.020z     2   
...       ...                       ...                       ...   ...   
10915002  ...  2017-04-27t10:08:48.102z  2020-12-08t09:44:59.088z     6   
10915305  ...  2015-02-23t10:29:00.543z  2020-11-30t21:58:07.439z     7   
10915495  ...  2015-03-10t16:45:31.974z  2020-12-11t00:00:01.060z     3   
10915820  ...  2018-01-26t02:18:25.551z  2020-11-24t05:37:24.167z     7   
10916306  ...  2017-03-30t17:08:15.383z  2020-12-09t16:16:50.762z     2   

         n_arxiv n_pmc  n_other_pids label primary_email_do

## URLs

In [28]:
def extract_url_domains(lst):
    domains = []
    for e in lst:
        # e[0] is a string describing the url
        # e[1] is the url
        domain = tldextract.extract(e[1])
        domains.append(domain.registered_domain)
    return domains

In [29]:
df['url_domains'] = df[df.urls.notna()]['urls'].apply(lambda x: extract_url_domains(x))

In [30]:
df[df['url_domains'].notna()].head()

orcid  claimed  verified_email  verified_primary_email  \
9    0000-0001-8718-0056        1               1                       1   
41   0000-0002-7845-4016        1               1                       1   
59   0000-0003-0967-6157        1               1                       1   
149  0000-0002-8015-3781        1               1                       1   
155  0000-0003-3444-936x        1               1                       1   

    given_names family_name  \
9           NaN         NaN   
41          NaN         NaN   
59          NaN         NaN   
149   alejandro     ossorio   
155  alessandra    caravale   

                                             biography other_names  \
9                                                  NaN       [飛資得]   
41                                                 NaN         NaN   
59                                                 NaN       [徐興慶]   
149                                                NaN         NaN   
155  archeologa, con laurea in metodologia e tecnic...         NaN   

                                                  urls  \
9    [[link1, http://orcid.flysheetmed.info], [ntu ...   
41   [[publication profile, http://publications.lib...   
59   [[ntu researcher profile, http://ah.ntu.edu.tw...   
149  [[web de la universidad carlos iii de madrid, ...   
155  [[isma- cnr, http://www.isma.cnr.it/?page_id=1...   

                  primary_email  ...          last_update_date n_doi n_arxiv  \
9    ericlin.flysheet@gmail.com  ...  2019-10-11t17:51:12.473z     0       0   
41                          NaN  ...  2016-06-06t15:29:36.952z     0       0   
59                          NaN  ...  2017-03-10t07:30:04.778z    12       0   
149         aossorio@di.uc3m.es  ...  2019-07-04t08:47:12.005z     0       0   
155                         NaN  ...  2020-05-14t15:54:38.235z     7       0   

    n_pmc n_other_pids  label primary_email_domain other_email_domains  \
9       0            6      1            gmail.com                 NaN   
41      0            0      0                  NaN                 NaN   
59      0            4      1                  NaN                 NaN   
149     0            0      0           di.uc3m.es                 NaN   
155     0           14      1                  NaN                 NaN   

    n_emails                     url_domains  
9        NaN  [flysheetmed.info, ntu.edu.tw]  
41       NaN                   [chalmers.se]  
59       NaN        [ntu.edu.tw, ntu.edu.tw]  
149      NaN                       [uc3m.es]  
155      NaN                        [cnr.it]  

[5 rows x 28 columns]

In [31]:
df['n_urls'] = df['url_domains'].str.len()

In [32]:
urls_by_orcid = df.sort_values('n_urls', ascending=False)[['orcid', 'n_urls']]
urls_by_orcid

orcid  n_urls
257375    0000-0002-1234-835x   219.0
3630067   0000-0001-7478-4539   174.0
5196089   0000-0002-7392-3792   169.0
10696059  0000-0002-6938-9638   152.0
6868932   0000-0002-5710-4041   114.0
...                       ...     ...
10916569  0000-0001-5692-7639     NaN
10916570  0000-0003-1539-0999     NaN
10916571  0000-0003-2858-5509     NaN
10916572  0000-0003-2438-9500     NaN
10916573  0000-0003-4119-4772     NaN

[10916574 rows x 2 columns]

In [33]:
set_top_n(100)
data = [
    go.Bar(
        x=urls_by_orcid[:TOP_N]['orcid'],
        y=urls_by_orcid[:TOP_N]['n_urls']
    )
]

layout = go.Layout(
    title='Top %s ORCID iDs with URLs' % TOP_N,
    xaxis=dict(tickangle=45, tickfont=dict(size=12), range=TOP_RANGE)
)
fig = go.Figure(data=data, layout=layout)
plotly.offline.iplot(fig)

In [34]:
top_urls = df[['orcid', 'url_domains']]\
                .explode('url_domains')\
                .reset_index(drop=True)\
                .groupby('url_domains')\
                .count()\
                .sort_values('orcid', ascending=False)

In [35]:
set_top_n(30)
data = [
    go.Bar(
        x=top_urls[:TOP_N].index,
        y=top_urls[:TOP_N]['orcid']
    )
]

layout = go.Layout(
    title='Top-%s URL domains' % TOP_N,
    xaxis=dict(tickangle=45, tickfont=dict(size=12), range=TOP_RANGE)
)
fig = go.Figure(data=data, layout=layout)
plotly.offline.iplot(fig)

## URLs speculation

In [36]:
df[(df['url_domains'].str.len() > 50) & (df['n_works'] > 0)]

orcid  claimed  verified_email  \
382497    0000-0002-9025-8632        1               1   
911811    0000-0002-4062-3603        1               1   
1136129   0000-0002-1929-6054        1               1   
3102686   0000-0003-2593-7134        1               1   
6868932   0000-0002-5710-4041        1               1   
8088987   0000-0002-9965-2425        1               1   
8658355   0000-0002-3920-7389        1               1   
8778864   0000-0002-3997-5070        1               1   
9980164   0000-0003-4948-9268        1               1   
10024501  0000-0003-2407-3557        1               1   
10091165  0000-0003-2183-8112        1               1   
10523205  0000-0003-2450-090x        1               1   
10696059  0000-0002-6938-9638        1               1   

          verified_primary_email         given_names        family_name  \
382497                         1         buycannabis         dispensary   
911811                         1       juan de dios   beltrán mancilla    
1136129                        1    franklin américo      canaza choque   
3102686                        1                 aan            jaelani   
6868932                        1             ryszard           romaniuk   
8088987                        1            jaroslaw           spychala   
8658355                        1                  а.              гусев   
8778864                        1  dr. parameshachari                b d   
9980164                        1            gustavo             duperré   
10024501                       1               abdul               aziz   
10091165                       1       pelayo munhoz               olea   
10523205                       1              eduard            babulak   
10696059                       1              adolfo    catral sanabria   

                                                  biography  \
382497    we procure and deliver premium cannabis strain...   
911811    juan de dios beltrán mancilla (*) filósofo aut...   
1136129   docente-investigador social. maestrando en der...   
3102686   all my papers can be downloaded from portal:re...   
6868932   professor of electronics and communications en...   
8088987   jaroslaw spychala has received a doctoral degr...   
8658355   surname, name gusev  alexander leonidovichdate...   
8778864   dr. parameshachari b dacm distinguished speake...   
9980164   gustavo norberto duperré graduated in arts and...   
10024501  abdul aziz was born on may 25, 1973, in brebes...   
10091165  pós-doutorado em gestão ambiental pela univers...   
10523205  professor eduard babulak is accomplished inter...   
10696059  my education is in computer science, mathemati...   

                                                other_names  \
382497    [we procure and deliver premium cannabis strai...   
911811    [juan de dios beltrán mancilla, filósofo autod...   
1136129   [franklin américo canaza-choque , franklin a. ...   
3102686                         [jaelani, a., jaelani, aan]   
6868932   [r.romaniuk, r.s.romaniuk, ryszard romaniuk, r...   
8088987                           [jaroslaw jozef spychala]   
8658355   [alexander l. gusev , alexander leonidovich gu...   
8778864                            [dr. parameshachari b d]   
9980164   [gustavo norberto duperré, duperré, g. n., gus...   
10024501  [abdul aziz, aziz, abdul, aziz, a., aziz, abd,...   
10091165  [ munhoz, pelayo olea,  olea, pelayo,  olea, p...   
10523205                         [professor eduard babulak]   
10696059                                                NaN   

                                                       urls  \
382497    [[find your cannabis & marijuana dispensary , ...   
911811    [[01.- juan de dios beltrán mancilla. teoría o...   
1136129   [[consejo nacional de ciencia, tecnología e in...   
3102686   [[microsoft academic research, https://academi...   
6868932   [[scholar google, http://scholar.google.pl/cit...   
8088987   [[resu

In [37]:
df[(df['url_domains'].str.len() > 10) & (df['n_works'] > 0) & (df['works_source'].str.len() == 1)]

orcid  claimed  verified_email  \
97666     0000-0002-7843-8497        1               1   
200670    0000-0003-1554-1531        1               1   
210325    0000-0003-3080-4643        1               1   
218947    0000-0003-3193-030x        1               1   
261974    0000-0002-5341-6531        1               1   
...                       ...      ...             ...   
10405738  0000-0002-3374-5709        1               1   
10472264  0000-0001-7228-5680        1               1   
10785961  0000-0002-3064-0194        1               1   
10845645  0000-0003-1047-4229        1               1   
10896059  0000-0003-4836-7074        1               1   

          verified_primary_email        given_names    family_name  \
97666                          1               davi        barbosa   
200670                         1          katarzyna         ochman   
210325                         1             graham         dawson   
218947                         1         juan pablo    wolff mejia   
261974                         1              trent        hammond   
...                          ...                ...            ...   
10405738                       1          guillermo          ortiz   
10472264                       1               text       protocol   
10785961                       1  leonardo fernando     cruz basso   
10845645                       1               bayu          sakti   
10896059                       1       karla haydee  ortiz palafox   

                                                  biography  \
97666     pesquisador na área sociojurídica, professor, ...   
200670    katarzyna ochman [kataˈʐɨna ˈɔxman] is assista...   
210325    science and engineering faculty (sef) libraria...   
218947    aspirante a maestría en derecho y negocios int...   
261974    mr trent hammond is an honorary research fello...   
...                                                     ...   
10405738  médico, internista, neumólogo, intensivista, e...   
10472264                                                NaN   
10785961                                                NaN   
10845645  bayu purbha saktisaya adalah bayu purbha sakti...   
10896059  karla haydee ortíz palafoxmiembro del sistema ...   

                                                other_names  \
97666                      [professor davi barbosa delmont]   
200670    [[kataˈʐɨna ˈɔxman], catharina ochman, cathari...   
210325                  [ graham colin dawson, g.c. dawson]   
218947    [juan pablo wolff, pablo wolff mejia, juan p. ...   
261974                 [trent ernest hammond (t.e.hammond)]   
...                                                     ...   
10405738                             [guillermo ortiz-ruiz]   
10472264                                                NaN   
10785961                                                NaN   
10845645                                [bayu purbha sakti]   
10896059                                    [karla palafox]   

                                                       urls  \
97666     [[plataforma de cursos ideia criativa, https:/...   
200670    [[researchgate, https://www.researchgate.net/p...   
210325    [[qut home page, https://www.library.qut.edu.a...   
218947    [[twitter, https://twitter.com/pablomejiam], [...   
261974    [[academic support masters, http://trenthammon...   
...                                                     ...   
10405738  [[elsevier, https://www.elsevier.com/], [asoci...   
10472264  [[about, https://about.me/textprotocol], [gith...   
10785961  [[papers-1, https://www.researchgate.net/profi...   
10845645  [[osf, http://osf.io/qe2ug], [inarxiv, https:/...   
10896059  [[opinión día del maestro, http://www.cronicaj...   

                                        primary_email  ... n_doi n_arxiv  \
97666                                             NaN  ...     0       0   
200670                                            NaN  ...     

In [38]:
exploded_sources = df[(df['url_domains'].str.len() > 10) & (df['n_works'] > 0) & (df['works_source'].str.len() == 1)].explode('works_source').reset_index(drop=True)
exploded_sources

orcid  claimed  verified_email  verified_primary_email  \
0    0000-0002-7843-8497        1               1                       1   
1    0000-0003-1554-1531        1               1                       1   
2    0000-0003-3080-4643        1               1                       1   
3    0000-0003-3193-030x        1               1                       1   
4    0000-0002-5341-6531        1               1                       1   
..                   ...      ...             ...                     ...   
136  0000-0002-3374-5709        1               1                       1   
137  0000-0001-7228-5680        1               1                       1   
138  0000-0002-3064-0194        1               1                       1   
139  0000-0003-1047-4229        1               1                       1   
140  0000-0003-4836-7074        1               1                       1   

           given_names    family_name  \
0                 davi        barbosa   
1            katarzyna         ochman   
2               graham         dawson   
3           juan pablo    wolff mejia   
4                trent        hammond   
..                 ...            ...   
136          guillermo          ortiz   
137               text       protocol   
138  leonardo fernando     cruz basso   
139               bayu          sakti   
140       karla haydee  ortiz palafox   

                                             biography  \
0    pesquisador na área sociojurídica, professor, ...   
1    katarzyna ochman [kataˈʐɨna ˈɔxman] is assista...   
2    science and engineering faculty (sef) libraria...   
3    aspirante a maestría en derecho y negocios int...   
4    mr trent hammond is an honorary research fello...   
..                                                 ...   
136  médico, internista, neumólogo, intensivista, e...   
137                                                NaN   
138                                                NaN   
139  bayu purbha saktisaya adalah bayu purbha sakti...   
140  karla haydee ortíz palafoxmiembro del sistema ...   

                                           other_names  \
0                     [professor davi barbosa delmont]   
1    [[kataˈʐɨna ˈɔxman], catharina ochman, cathari...   
2                  [ graham colin dawson, g.c. dawson]   
3    [juan pablo wolff, pablo wolff mejia, juan p. ...   
4                 [trent ernest hammond (t.e.hammond)]   
..                                                 ...   
136                             [guillermo ortiz-ruiz]   
137                                                NaN   
138                                                NaN   
139                                [bayu purbha sakti]   
140                                    [karla palafox]   

                                                  urls  \
0    [[plataforma de cursos ideia criativa, https:/...   
1    [[researchgate, https://www.researchgate.net/p...   
2    [[qut home page, https://www.library.qut.edu.a...   
3    [[twitter, https://twitter.com/pablomejiam], [...   
4    [[academic support masters, http://trenthammon...   
..                                                 ...   
136  [[elsevier, https://www.elsevier.com/], [asoci...   
137  [[about, https://about.me/textprotocol], [gith...   
138  [[papers-1, https://www.researchgate.net/profi...   
139  [[osf, http://osf.io/qe2ug], [inarxiv, https:/...   
140  [[opinión día del maestro, http://www.cronicaj...   

                                   primary_email  ... n_doi n_arxiv n_pmc  \
0                                            NaN  ...     0       0     0   
1                                            NaN  ...     1       0     0   
2                            g.dawson@qut.edu.au  ...     0       0     0   
3                  juanpmejia@ulasallista.edu.co  ...     0       0     0   
4    trent.hammond@academicsupportmasters.com.au  ...     1       0     0   
..                                           ...

In [39]:
exploded_sources[exploded_sources.apply(lambda x: x['works_source'].find(x['given_names']) >= 0, axis=1)]

orcid  claimed  verified_email  verified_primary_email  \
0    0000-0002-7843-8497        1               1                       1   
1    0000-0003-1554-1531        1               1                       1   
3    0000-0003-3193-030x        1               1                       1   
4    0000-0002-5341-6531        1               1                       1   
5    0000-0001-5295-2271        1               1                       1   
..                   ...      ...             ...                     ...   
135  0000-0002-8125-0081        1               1                       1   
136  0000-0002-3374-5709        1               1                       1   
137  0000-0001-7228-5680        1               1                       1   
139  0000-0003-1047-4229        1               1                       1   
140  0000-0003-4836-7074        1               1                       1   

      given_names    family_name  \
0            davi        barbosa   
1       katarzyna         ochman   
3      juan pablo    wolff mejia   
4           trent        hammond   
5         antoniy         moysey   
..            ...            ...   
135         issam      bencheikh   
136     guillermo          ortiz   
137          text       protocol   
139          bayu          sakti   
140  karla haydee  ortiz palafox   

                                             biography  \
0    pesquisador na área sociojurídica, professor, ...   
1    katarzyna ochman [kataˈʐɨna ˈɔxman] is assista...   
3    aspirante a maestría en derecho y negocios int...   
4    mr trent hammond is an honorary research fello...   
5                                                  NaN   
..                                                 ...   
135                                                NaN   
136  médico, internista, neumólogo, intensivista, e...   
137                                                NaN   
139  bayu purbha saktisaya adalah bayu purbha sakti...   
140  karla haydee ortíz palafoxmiembro del sistema ...   

                                           other_names  \
0                     [professor davi barbosa delmont]   
1    [[kataˈʐɨna ˈɔxman], catharina ochman, cathari...   
3    [juan pablo wolff, pablo wolff mejia, juan p. ...   
4                 [trent ernest hammond (t.e.hammond)]   
5                                                  NaN   
..                                                 ...   
135                  [issame1982, دكتور عصام بن الشيخ]   
136                             [guillermo ortiz-ruiz]   
137                                                NaN   
139                                [bayu purbha sakti]   
140                                    [karla palafox]   

                                                  urls  \
0    [[plataforma de cursos ideia criativa, https:/...   
1    [[researchgate, https://www.researchgate.net/p...   
3    [[twitter, https://twitter.com/pablomejiam], [...   
4    [[academic support masters, http://trenthammon...   
5    [[academic journals database, http://journalda...   
..                                                 ...   
135  [[my blog web site, http://issame1982.blogspot...   
136  [[elsevier, https://www.elsevier.com/], [asoci...   
137  [[about, https://about.me/textprotocol], [gith...   
139  [[osf, http://osf.io/qe2ug], [inarxiv, https:/...   
140  [[opinión día del maestro, http://www.cronicaj...   

                                   primary_email  ... n_doi n_arxiv n_pmc  \
0                                            NaN  ...     0       0     0   
1                                            NaN  ...     1       0     0   
3                  juanpmejia@ulasallista.edu.co  ...     0       0     0   
4    trent.hammond@academicsupportmasters.com.au  ...     1       0     0   
5                      antoniimoisei@bsmu.edu.ua  ...     0       0     0   
..                                           ...  ...   ...     ...   ...   
135                            

## Works source

Paste from Miriam

## External IDs

External IDs should come from reliable sources. ORCiD registrants cannot add them freely.

In [40]:
df['n_ids'] = df[df['external_ids'].notna()].external_ids.str.len()

In [41]:
df.n_ids.describe()

count    1.301959e+06
mean     1.358640e+00
std      6.635087e-01
min      1.000000e+00
25%      1.000000e+00
50%      1.000000e+00
75%      2.000000e+00
max      8.000000e+01
Name: n_ids, dtype: float64

In [42]:
df[df.n_ids == df.n_ids.max()]

orcid  claimed  verified_email  verified_primary_email  \
7253330  0000-0002-9554-6633        1               1                       1   

        given_names family_name biography other_names  \
7253330      john a    williams       NaN         NaN   

                                                      urls primary_email  ...  \
7253330  [[aston university profile page, https://resea...           NaN  ...   

        n_arxiv n_pmc n_other_pids label primary_email_domain  \
7253330       0     0          208     1                  NaN   

         other_email_domains n_emails    url_domains n_urls  n_ids  
7253330                  NaN      NaN  [aston.ac.uk]    1.0   80.0  

[1 rows x 30 columns]

In [43]:
ids = df[['orcid', 'external_ids']].explode('external_ids').reset_index(drop=True)

In [44]:
ids['provider'] = ids[ids.external_ids.notna()]['external_ids'].apply(lambda x: x[0])

In [45]:
ids[ids.provider.notna()].head()

orcid                     external_ids          provider
7   0000-0001-7463-977x           [loop profile, 371409]      loop profile
9   0000-0001-8718-0056  [scopus author id, 55466912100]  scopus author id
10  0000-0001-8718-0056   [scopus author id, 7102015452]  scopus author id
14  0000-0001-9708-5570      [researcherid, p-5112-2015]      researcherid
15  0000-0001-9708-5570  [scopus author id, 42062216900]  scopus author id

In [46]:
top_ids_providers = ids.groupby('provider').count().sort_values('orcid', ascending=False)

In [47]:
data = [
    go.Bar(
        x=top_ids_providers.index,
        y=top_ids_providers['orcid']
    )
]

layout = go.Layout(
    title='IDs provided by providers',
    xaxis=dict(tickangle=45, tickfont=dict(size=12))
)
fig = go.Figure(data=data, layout=layout)
plotly.offline.iplot(fig)

In [48]:
pd.unique(ids['provider'])

array([nan, 'loop profile', 'scopus author id', 'researcherid',
       'scopus author id: ', 'gnd', 'isni', 'ciência id', 'pitt id',
       'id dialnet', 'technical university of denmark cwis',
       'researcher name resolver id', 'scopus author id:',
       'hkust profile', '中国科学家在线', 'cti vitae', 'escientist',
       'researcher id', 'sciprofile', 'digital author id', 'scopus  id',
       'uow scholars', 'authenticusid', 'authenticus', 'authid',
       'hku researcherpage', 'chalmers id', 'iauthor', 'us epa vivo',
       'digital author id (dai)', 'vivo cornell', 'smithsonian profiles',
       'github', 'google scholar', 'scopus id', 'researcherid:', 'dai',
       'kaken', 'orcid id', 'dialnet id', 'profile system identifier',
       'sciprofiles', 'id dialnet:', 'researcherid: ', 'scienceopen',
       'une researcher id', 'custom', 'orcid'], dtype=object)

## Keywords

This field is problematic as users can be nasty and put multiple keywords in one as opposed of having different keywords. Look this

In [49]:
df[df['orcid'] == AM]['keywords'].values[0]

['data science ',
 'science of science',
 'scholarly knowledge mining',
 'open science',
 'research infrastructures']

I did a good job. The following instead is dirty

In [50]:
df[df['orcid'] == PP]['keywords'].values[0]

['open access, open science, libraries, repositories, social web,']

So the keyword field needs some cleaning

In [51]:
def fix_keywords(lst):
        fixed = set()
        for k in lst:
            tokens = set(k.split(','))
#             tokens.remove('')
            for t in tokens:
                fixed.add(str.strip(t))
        fixed.discard('')
        return list(fixed)

In [52]:
df['fixed_keywords'] = df[df.keywords.notna()]['keywords'].apply(lambda x: fix_keywords(x))

In [53]:
df[df['orcid'] == PP]['fixed_keywords'].values[0]

['open science', 'repositories', 'social web', 'libraries', 'open access']

In [54]:
df['n_keywords'] = df.keywords.str.len()

In [55]:
keywords_by_orcid = df.sort_values('n_keywords', ascending=False)[['orcid', 'n_keywords']]
keywords_by_orcid

orcid  n_keywords
2851081   0000-0002-0673-0341       154.0
7344151   0000-0002-7060-4112       141.0
2235440   0000-0002-6075-3501       140.0
2994233   0000-0002-4071-0301       118.0
3971323   0000-0002-9638-8091       115.0
...                       ...         ...
10916569  0000-0001-5692-7639         NaN
10916570  0000-0003-1539-0999         NaN
10916571  0000-0003-2858-5509         NaN
10916572  0000-0003-2438-9500         NaN
10916573  0000-0003-4119-4772         NaN

[10916574 rows x 2 columns]

In [56]:
set_top_n(100)
data = [
    go.Bar(
        x=keywords_by_orcid[:TOP_N]['orcid'],
        y=keywords_by_orcid[:TOP_N]['n_keywords']
    )
]

layout = go.Layout(
    title='Keywords provided by ORCiD',
    xaxis=dict(tickangle=45, tickfont=dict(size=12), range=TOP_RANGE)
)
fig = go.Figure(data=data, layout=layout)
plotly.offline.iplot(fig)

In [57]:
top_keywords = df[['orcid', 'keywords']]\
                .explode('keywords')\
                .reset_index(drop=True)\
                .groupby('keywords')\
                .count()\
                .sort_values('orcid', ascending=False)

In [58]:
set_top_n(50)
data = [
    go.Bar(
        x=top_keywords[:TOP_N].index,
        y=top_keywords[:TOP_N]['orcid']
    )
]

layout = go.Layout(
    title='Top-%s keywords occurrence' % TOP_N,
    xaxis=dict(tickangle=45, tickfont=dict(size=12))
)
fig = go.Figure(data=data, layout=layout)
plotly.offline.iplot(fig)

## Correlation

In [59]:
fig = px.imshow(df[df.n_ids > 0].corr())
fig.show()